## Tech Challenge
Tech Challenge é o projeto que englobará os conhecimentos obtidos em
todas as disciplinas da fase. Esta é uma atividade que, em princípio, deve ser
desenvolvida em grupo. É importante atentar-se ao prazo de entrega, pois trata-
se de uma atividade obrigatória, uma vez que sua pontuação se refere a 90% da
nota final.

## O problema
Imagine agora que você foi contratado(a) como Expert em Data Analytics
por um grande hospital para entender como foi o comportamento da população
na época da pandemia da COVID-19 e quais indicadores seriam importantes
para o planejamento, caso haja um novo surto da doença.
Apesar de ser contratado(a) agora, a sua área observou que a utilização
do estudo do PNAD-COVID 19 do IBGE seria uma ótima base para termos boas
respostas ao problema proposto, pois são dados confiáveis. Porém, não será
necessário utilizar todas as perguntas realizadas na pesquisa para enxergar
todas as oportunidades ali postas.
É sempre bom ressaltar que há dados triviais que precisam estar no
projeto, pois auxiliam muito na análise dos dados:
 - •Características clínicas dos sintomas;
 - • Características da população;
 - • Características econômicas da sociedade.
O Head de Dados pediu para que você entrasse na base de dados do
PNAD-COVID-19 do IBGE (https://covid19.ibge.gov.br/pnad-covid/) e
organizasse esta base para análise, utilizando Banco de Dados em Nuvem e
trazendo as seguintes características:
 - a. Utilização de no máximo 20 questionamentos realizados na
 - b. pesquisa; Utilizar 3 meses para construção da solução.
 - c. d. Caracterização dos sintomas clínicos da população.Comportamento da população na época da COVID-19;
- e. Características econômicas da Sociedade.

Seu objetivo será trazer uma breve análise dessas informações, como foi
a organização do banco, as perguntas selecionadas para a resposta do problema
e quais seriam as principais ações que o hospital deverá tomar em caso de um
novo surto de COVID-19

*Dica*: leiam com atenção a base de dados e toda a documentação que o
site o PNAD – Covid19 traz, principalmente os dicionários, que ajudam e muito
no entendimento da Base de Dados.

*Dica 2*: utilizem o que já foi ensinado e consolidado nas outras fases para
apresentar a resolução do projeto

## Dicionario de dados

Para este desafio, selecionamos apenas as colunas que fazem sentido para a nossa análise. Essas variáveis são fundamentais para o desenvolvimento e direcionamento das nossas conclusões.

- Ano: Ano da pesquisa
- UF: Unidade da Federacao
- Estrato : Estrato
- UPA : UPA
- V1013 : Mês da pesquisa
- A001B1 : Dia do nascimento
- A001B2 : Mes do nascimento
- A001B3 : Ano do nascimento
- A002: Idade do morador
- A003: Sexo
- B0011: Teve Febre
- B0012: Teve tosse
- B0013: dor de garganta
- B0014: Dificuldade de respirar
- B0015: dor de cabeca
- B0016: dor no peito
- B00111: perca do paladar e cheiro
- B002: foi ao medico?
- B0031: ficou em casa
- B005: ficou internado
- B006: ficou entubado
- B008: fez o teste
- B009A: fez o teste (SWAB)
- B009B: resultado do teste
- B009C: furo no dedo
- B009D: resultado teste sangue
- B009E: coletou sangue e fez teste
- B009F: Qual o resultado?
- B0101: diabetes
- B0102: hipertensao
- B0103: doencas respiratorias
- B0104: doenas cardiacas








### Importando as Bibilotecas

In [0]:
from pyspark import SparkConf
from pyspark.sql import SparkSession
from pyspark.sql import functions as f
from pyspark.sql import Row, DataFrame
from pyspark.sql.types import StringType, StructType, StructField, IntegerType
from pyspark.sql.functions import col, expr, lit, substring, concat, concat_ws, when, coalesce,sum,to_date, upper, countDistinct, avg,count,first
from functools import reduce
import pandas as pd
import numpy as np
import os
from datetime import datetime, timedelta
import seaborn as sns
import matplotlib.pyplot as plt
import warnings
import urllib.request
import pyspark.pandas as ps
import requests
import tarfile
from io import BytesIO
warnings.filterwarnings('ignore')

## Criando a base

 - Carregaremos os três arquivos .csv com os dados brutos
 - Unificaremos os arquivos em uma única base com as colunas relevantes para a análise
- Em seguida, aplicaremos os dicionários para ajustar e interpretar os dados

In [0]:
# Configuração comum
file_type = "csv"
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","  

# SETEMBRO
df_set = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load("/FileStore/tables/SETEMBRO20-3.csv")

# OUTUBRO
df_out = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load("/FileStore/tables/OUTUBRO20-3.csv")

# NOVEMBRO
df_nov = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load("/FileStore/tables/NOVEMBRO20-3.csv")

### selecionando apenas as colunas que vamos usar e depois criando uma base final.

In [0]:
df_set = df_set.select("Ano", "UF","Estrato","UPA","V1013","A001B1", "A001B2", "A001B3","A002","A003", "A004", "A005", "B0011", "B0012", "B0013", "B0014","B0015","B0016","B0017","B0018","B0019","B002", "B0031","B005","B006","B008","B009A","B009B","B009C","B009D","B009E","B009F","B0101","B0102","B0103","B0104","B0105","B0106", "B00111")
df_out = df_out.select("Ano", "UF","Estrato","UPA","V1013","A001B1", "A001B2", "A001B3","A002","A003", "A004", "A005", "B0011", "B0012", "B0013", "B0014","B0015","B0016","B0017","B0018","B0019","B002", "B0031","B005","B006","B008","B009A","B009B","B009C","B009D","B009E","B009F","B0101","B0102","B0103","B0104","B0105","B0106", "B00111")
df_nov = df_nov.select("Ano", "UF","Estrato","UPA","V1013","A001B1", "A001B2", "A001B3","A002","A003", "A004", "A005", "B0011", "B0012", "B0013", "B0014","B0015","B0016","B0017","B0018","B0019","B002", "B0031","B005","B006","B008","B009A","B009B","B009C","B009D","B009E","B009F","B0101","B0102","B0103","B0104","B0105","B0106", "B00111")

base = df_set.unionByName(df_out).unionByName(df_nov)

#### Tratamento de Dados Ausentes
Alguns campos estão vazios devido à ausência de resposta. Para evitar que o DataFrame contenha valores nulos, estamos preenchendo com zero. Essa substituição é apenas estrutural e não impacta os resultados da análise.

In [0]:
# Conta nulos por coluna
df_nulls = base.select([
    sum(when(col(c).isNull(), 1).otherwise(0)).alias(c)
    for c in base.columns
])

# Converte para pandas e transpoe pra ficar visual
df_nulls_pd = df_nulls.toPandas().T.reset_index()
df_nulls_pd.columns = ['coluna', 'valores_nulos']
display(df_nulls_pd)

coluna valores_nulos Ano 0 UF 0 Estrato 0 UPA 0 V1013 0 A001B1 0 A001B2 0 A001B3 0 A002 0 A003 0 A004 0 A005 0 B0011 0 B0012 0 B0013 0 B0014 0 B0015 0 B0016 0 B0017 0 B0018 0 B0019 0 B002 1104247 B0031 1116056 B005 1143367 B006 1148618 B008 0 B009A 1015655 B009B 1098266 B009C 1015655 B009D 1086297 B009E 1015655 B009F 1110474 B0101 0 B0102 0 B0103 0 B0104 0 B0105 0 B0106 0 B00111 0

In [0]:
base = base.fillna(0)

In [0]:
## contando o tamanho da nossa base
base.count()

Out[6]: 1149197

In [0]:
## criando uma temp view 
base.createOrReplaceTempView("tb_base")

## Base

Optamos por utilizar apenas os moradores que de fato tiveram diagnóstico positivo. Com esses dados, buscamos identificar padrões de sintomas recorrentes e, a partir disso, propor estratégias de prevenção mais eficazes para possíveis cenários futuros.

Utilizaremos técnicas de SQL para conduzir as análises, convertendo também os campos numéricos em seus respectivos significados conforme definidos no dicionário de dados.

In [0]:

new_base = spark.sql( """
    SELECT 
    ANO AS ANO
    ,CASE
      WHEN UF = 11 THEN 'Rondônia'
      WHEN UF = 12 THEN 'Acre'
      WHEN UF = 13 THEN 'Amazonas'
      WHEN UF = 14 THEN 'Roraima'
      WHEN UF = 15 THEN 'Pará'
      WHEN UF = 16 THEN 'Amapá'
      WHEN UF = 17 THEN 'Tocantins'
      WHEN UF = 21 THEN 'Maranhão'
      WHEN UF = 22 THEN 'Piauí'
      WHEN UF = 23 THEN 'Ceará'
      WHEN UF = 24 THEN 'Rio Grande do Norte'
      WHEN UF = 25 THEN 'Paraíba'
      WHEN UF = 26 THEN 'Pernambuco'
      WHEN UF = 27 THEN 'Alagoas'
      WHEN UF = 28 THEN 'Sergipe'
      WHEN UF = 29 THEN 'Bahia'
      WHEN UF = 31 THEN 'Minas Gerais'
      WHEN UF = 32 THEN 'Espírito Santo'
      WHEN UF = 33 THEN 'Rio de Janeiro'
      WHEN UF = 35 THEN 'São Paulo'
      WHEN UF = 41 THEN 'Paraná'
      WHEN UF = 42 THEN 'Santa Catarina'
      WHEN UF = 43 THEN 'Rio Grande do Sul'
      WHEN UF = 50 THEN 'Mato Grosso do Sul'
      WHEN UF = 51 THEN 'Mato Grosso'
      WHEN UF = 52 THEN 'Goiás'
      WHEN UF = 53 THEN 'Distrito Federal'
      ELSE 'Desconhecido'
END AS UF
,estrato
,UPA
,CASE V1013 
  WHEN 1 THEN "Janeiro"
  WHEN 2 THEN "Fevereiro"
  WHEN 3 THEN "Março"
  WHEN 4 THEN "Abril"
  WHEN 5 THEN "Maio"
  WHEN 6 THEN "Junho"
  WHEN 7 THEN "Julho"
  WHEN 8 THEN "Agosto"
  WHEN 9 THEN "Setembro"
  WHEN 10 THEN "Outubro"
  WHEN 11 THEN "Novembro"
  when 12 then "Dezembro"
    END NM_MES
  ,concat(A001B1,A001B2,A001B3 ) as DT_NASCIMENTO
  ,A002 as IDADE
  ,CASE A003
    WHEN 1 THEN "Masculino"
    WHEN 2 THEN "Feminino"
    END SEXO
  ,CASE A004
    WHEN 1 THEN "Branca"
    WHEN 2 THEN "Preta"
    WHEN 3 THEN "Amarela"
    WHEN 4 THEN "Parda"
    WHEN 5 THEN "Indigena"
    ELSE "Ignorado"
      END RACA
  ,CASE A005
    WHEN 1 THEN "Sem instrução"
    WHEN 2 THEN "Fundamental incompleto"
    WHEN 3 THEN "Fundamental completa"
    WHEN 4 THEN "Médio incompleto"
    WHEN 5 THEN "Médio completo"
    WHEN 6 THEN "Superior incompleto"
    WHEN 7 THEN "Superior completo"
    WHEN 8 THEN "Pós-graduação, mestrado ou doutorado"
      END ESCOLARIDADE
  ,CASE B0011 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" WHEN 3 THEN "Nao sabe" ELSE "Ignorado" END FEBRE
  ,CASE B0012 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" WHEN 3 THEN "Nao sabe" ELSE "Ignorado" END TOSSE
  ,CASE B0013 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" WHEN 3 THEN "Nao sabe" ELSE "Ignorado" END DOR_GARGANTA
  ,CASE B0014 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" WHEN 3 THEN "Nao sabe" ELSE "Ignorado" END DIFICULDADE_RESPIRAR
  ,CASE B0015 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" WHEN 3 THEN "Nao sabe" ELSE "Ignorado" END DOR_CABECA
  ,CASE B0016 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" WHEN 3 THEN "Nao sabe" ELSE "Ignorado" END DOR_PEITO
  ,CASE B0017 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" WHEN 3 THEN "Nao sabe" ELSE "Ignorado" END NAUSEA
  ,CASE B0018 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" WHEN 3 THEN "Nao sabe" ELSE "Ignorado" END NARIZ_ENTUPIDO
  ,CASE B0019 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" WHEN 3 THEN "Nao sabe" ELSE "Ignorado" END FADIGA
  ,CASE B00111 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" WHEN 3 THEN "Nao sabe" ELSE "Ignorado" END FALTA_AR
  ,CASE B002 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END IR_AO_MEDICO
  ,CASE B0031 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END FICOU_EM_CASA
  ,CASE B005 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" WHEN 3 THEN "Nao foi atendido" ELSE "Ignorado" END FICOU_INTERNADO
  ,CASE B006 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END FICOU_SEDADO
  ,CASE B008 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END REALIZOU_TESTE
  ,CASE B009A WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END EXAME_COTONETE
  ,B009B AS RESULTADO_COTONETE
  ,CASE B009A WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END EXAME_SANGUE_DED0
  ,B009D AS RESULTADO_SANGUE_DEDO
  ,CASE B009E WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END EXAME_SANGUE
  ,B009F AS RESULTADO_SANGUE
  ,CASE B0101 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END DIABETE
  ,CASE B0102 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END HIPERTENSAO
  ,CASE B0103 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END DOENCA_RESPIRATORIA
  ,CASE B0104 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END DOENCA_CARDIACA
  ,CASE B0105 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END DEPRESSAO
  ,CASE B0106 WHEN 1 THEN "Sim" WHEN 2 THEN "Nao" ELSE "Ignorado" END CANCER
  
FROM tb_base

WHERE B009B = 1 OR B009D = 1 OR B009F = 1

""")


In [0]:
display(new_base)

ANO UF estrato UPA NM_MES DT_NASCIMENTO IDADE SEXO RACA ESCOLARIDADE FEBRE TOSSE DOR_GARGANTA DIFICULDADE_RESPIRAR DOR_CABECA DOR_PEITO NAUSEA NARIZ_ENTUPIDO FADIGA FALTA_AR IR_AO_MEDICO FICOU_EM_CASA FICOU_INTERNADO FICOU_SEDADO REALIZOU_TESTE EXAME_COTONETE RESULTADO_COTONETE EXAME_SANGUE_DED0 RESULTADO_SANGUE_DEDO EXAME_SANGUE RESULTADO_SANGUE DIABETE HIPERTENSAO DOENCA_RESPIRATORIA DOENCA_CARDIACA DEPRESSAO CANCER 2020 Rondônia 1110011 110015970 Setembro 99999999 36 Feminino Parda Superior completo Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Sim 1 Sim 2 Sim 1 Nao Nao Nao Nao Nao Nao 2020 Rondônia 1110011 110015970 Setembro 2011970 50 Feminino Parda Fundamental incompleto Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Nao 0 Nao 1 Sim 1 Nao Sim Nao Nao Nao Nao 2020 Rondônia 1110011 110015970 Setembro 2231975 45 Masculino Parda Fundamental incompleto Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Nao 0 Nao 1 Sim 1 Nao Nao Nao Nao Nao Nao 2020 Rondônia 1110011 110011734 Setembro 1091988 32 Feminino Parda Médio incompleto Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Sim 3 Sim 0 Sim 1 Nao Nao Nao Nao Nao Nao 2020 Rondônia 1110011 110011734 Setembro 451992 28 Masculino Parda Médio incompleto Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Sim 1 Sim 0 Sim 2 Nao Nao Nao Nao Nao Nao 2020 Rondônia 1110011 110011734 Setembro 3091981 38 Feminino Parda Médio completo Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Sim 1 Sim 1 Sim 1 Nao Nao Nao Nao Nao Nao 2020 Rondônia 1110011 110017231 Setembro 4101962 57 Masculino Branca Superior completo Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Nao 0 Nao 1 Sim 1 Nao Nao Nao Nao Nao Nao 2020 Rondônia 1110011 110017231 Setembro 3121963 56 Feminino Preta Médio completo Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Nao 0 Nao 1 Sim 1 Nao Sim Sim Nao Nao Nao 2020 Rondônia 1110011 110017231 Setembro 1831999 21 Masculino Preta Superior incompleto Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Nao 0 Nao 1 Sim 1 Nao Nao Nao Nao Nao Nao 2020 Rondônia 1110011 110009452 Setembro 271998 22 Masculino Parda Superior incompleto Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Sim 1 Sim 0 Nao 0 Nao Nao Nao Nao Nao Nao 2020 Rondônia 1110011 110020020 Setembro 131981 39 Feminino Branca Médio completo Sim Sim Sim Sim Sim Sim Sim Sim Sim Nao Nao Sim Ignorado Ignorado Sim Sim 1 Sim 0 Nao 0 Nao Nao Nao Nao Sim Nao 2020 Rondônia 1110011 110020020 Setembro 10101981 38 Masculino Preta Médio completo Nao Sim Sim Sim Sim Sim Sim Sim Sim Nao Sim Ignorado Nao Ignorado Sim Sim 1 Sim 0 Nao 0 Nao Sim Nao Nao Nao Nao 2020 Rondônia 1110011 110015683 Setembro 20111986 33 Masculino Parda Superior completo Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Nao 0 Nao 1 Sim 1 Nao Nao Nao Nao Nao Nao 2020 Rondônia 1110011 110019780 Setembro 28121973 46 Feminino Parda Fundamental incompleto Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Sim 1 Sim 0 Nao 0 Sim Sim Nao Nao Nao Nao 2020 Rondônia 1110011 110019780 Setembro 1611998 22 Feminino Parda Médio completo Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Sim 1 Sim 0 Nao 0 Nao Nao Nao Nao Nao Nao 2020 Rondônia 1110011 110013678 Setembro 11101976 43 Masculino Parda Superior completo Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Sim 1 Sim 0 Sim 3 Nao Sim Nao Nao Nao Nao 2020 Rondônia 1110011 110013678 Setembro 12101976 43 Feminino Parda Superior completo Nao Nao Nao Nao Nao Nao Nao Nao Nao Nao Ignorado Ignorado Ignorado Ignorado Sim Nao 0 Nao 0 Sim 1 Nao Sim Nao Nao Sim Nao 2020 Rondônia 1110011 110013678 Setembro 3101939 80 Masculino Pa

In [0]:
new_base.count()

Out[10]: 32922

## Insights

Agora vamos realizar a análise de insights no Power BI. Para isso, exportaremos o arquivo em formato CSV e, em seguida, construiremos os dashboards e visualizações na ferramenta.
